In [1]:
import pandas as pd
import matplotlib.pyplot as plt

In [2]:
import os
import numpy as np
import warnings
import sys
import pickle
sys.path.append('../')
warnings.filterwarnings("ignore")

from src.kernels import rbf
from src.acquisition_func import ucb
from src.gaussian_process import Gaussain_Process
from src.bayesopt import Bayesopt
from load_exp_data import stress_resist_data_loader, append_new_data

%load_ext autoreload
%autoreload 2

In [3]:
DATA_DIR = "/home/ashriva/work/beyond_finger_printing/ankit/Experiments/Data/raw/new_bayes_exp/"
RESULT_DIR = "/home/ashriva/work/beyond_finger_printing/ankit/Experiments/Results/design_of_experiments/final_run/"

In [6]:
run = 9

## 3D view

In [63]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from plotly.offline import plot

def add_3dsurf_plot(n, fig, param_grid, val, param_obs, val_obs, next_point, name, ax_num):

    shape = param_grid.shape[1:]
    
    val_min = -np.max(val)
    val_max = np.max(val)
    
    x = param_grid[0]
    y = param_grid[1]
    z = val.reshape(shape)
    _, fig_ncols = fig._get_subplot_rows_columns()
    fig_ncols = len(fig_ncols) 
    fig.add_trace(go.Surface(x=x, y=y, z=z, 
                             showscale=True,
                             colorbar=dict(x=ax_num/fig_ncols-.1/fig_ncols),
#                              contours={
#                                  "z": {"show": True, "start": val_min, "end": val_max, "size": 200, 
#                                        "width": 1, "color": 'black'} # add <"usecolormap": True>
#                                     }, 
                             opacity=0.75, 
                             cmin=val_min, 
                             cmax=val_max), row=1, col=ax_num) 
    
    step = 1
    X = param_grid[0][::step,::step]
    Y = param_grid[1][::step,::step]
    Z = val.reshape(shape)[::step,::step]
    line_marker = dict(color='#101010', width=1)
    for xx, yy, zz in zip(X, Y, Z):
        fig.add_trace(go.Scatter3d(x=xx, y=yy, z=zz, mode='lines', line=line_marker, showlegend=False),
                      row=1, col=ax_num)

    X = X.T
    Y = Y.T
    Z = Z.T
    for xx, yy, zz in zip(X, Y, Z):
        fig.add_trace(go.Scatter3d(x=xx, y=yy, z=zz, mode='lines', line=line_marker, showlegend=False),
                      row=1, col=ax_num)

    if(n == 0):
        fig.add_trace(go.Scatter3d(x=param_obs[:,0], y=param_obs[:,1], z=val_obs[:,0], 
                          mode='markers',
                          marker=dict(size=2, color='red'),
                          showlegend=False,
                         ),
                        row=1, col=ax_num)      
        
    else:
        fig.add_trace(go.Scatter3d(x=param_obs[:-3, 0], y=param_obs[:-3, 1], z=val_obs[:-3,0], 
                          mode='markers',
                          marker=dict(size=2, color='red'),
                          showlegend=False,
                         ),
                        row=1, col=ax_num)

        fig.add_trace(go.Scatter3d(x=param_obs[-3:, 0], y=param_obs[-3:, 1], z=val_obs[-3:,0], 
                          mode='markers',
                          marker=dict(size=2, color='green'),
                          showlegend=False,
                         ),
                        row=1, col=ax_num)
    
    fig.add_trace(go.Scatter3d(x=next_point[:1, 0], y=next_point[:1, 1], z=next_point[:1, 2], 
                      mode='markers',
                      marker=dict(size=2, color='blue'),
                      showlegend=False,
                     ),
                    row=1, col=ax_num)

    return val_min, val_max

In [64]:
fig = make_subplots(
        rows=1, cols=3,
        subplot_titles = ['Stress', 'Stress gradient' ,'Resistance'],
        specs=[[{'type': 'surface'}, {'type': 'surface'}, {'type': 'surface'}]],
#         print_grid=True
        )

X_obs = np.load(RESULT_DIR + "/" + str(run) + "_x_obs.npy")
xgrid = np.load(RESULT_DIR + "/" + str(run) + "_xgrid.npy")
ygrid = np.load(RESULT_DIR + "/" + str(run) + "_ygrid.npy")
x_suggested = np.load(RESULT_DIR+"/"+str(run)+'_x_next.npy')

parameter_grid = np.array([xgrid, ygrid])

# Plot stress
stress_mu_array = np.load(RESULT_DIR + "/" + str(run) + "_stress_mu_array.npy")
stress_Y_obs = np.load(RESULT_DIR + "/" + str(run) + "_y_stress_obs.npy")

with open(RESULT_DIR + "/" + str(run) + '_gp_objects.pkl', 'rb') as file:
    data = pickle.load(file)
    GP_stress = data['stress'] 
    mu, _, mu_grad = GP_stress.posterior(x_suggested, calc_grad=True)

val_min, val_max = add_3dsurf_plot(run, fig, 
                                   parameter_grid, stress_mu_array, 
                                   X_obs, stress_Y_obs, 
                                   np.append(x_suggested, mu, axis=1), 
                                   'stress', 1)
scene1 = dict(zaxis = dict(nticks=4, range=[-2000, 2000],),
             xaxis_title_text = 'Pressure',
             yaxis_title_text = 'Power',
             zaxis_title_text = 'Stress',
            )

# Plots stress gradient
stress_grad_array = np.load(RESULT_DIR + "/" + str(run) + "_obj_array1.npy")
stress_grad_array = (-stress_grad_array + 1) * 1900
_, _, mu_grad_obs = GP_stress.posterior(X_obs, calc_grad=True)

val_min, val_max = add_3dsurf_plot(run, fig, 
                                   parameter_grid, stress_grad_array, 
                                   X_obs, mu_grad_obs, 
                                   np.append(x_suggested, mu_grad, axis=1), 
                                   'stress gradient', 2)
scene2 = dict(zaxis = dict(nticks=4, range=[-1000, 1500],),
             xaxis_title_text = 'Pressure',
             yaxis_title_text = 'Power',
             zaxis_title_text = 'Stress gradient',
            )

# Plot Resistance

resist_mu_array = np.load(RESULT_DIR + "/" + str(run) + "_resist_mu_array.npy")
resist_Y_obs = np.load(RESULT_DIR + "/" + str(run) + "_y_resist_obs.npy")

with open(RESULT_DIR + "/" + str(run) + '_gp_objects.pkl', 'rb') as file:
    data = pickle.load(file)
    GP_resist = data['resist']    
    mu, _ = GP_resist.posterior(x_suggested)

val_min, val_max = add_3dsurf_plot(run, fig, 
                                   parameter_grid, resist_mu_array, 
                                   X_obs, resist_Y_obs, 
                                   np.append(x_suggested, mu, axis=1),
                                   'resist', 3)
scene3 = dict(zaxis = dict(nticks=4, range=[0, 100],),
             xaxis_title_text = 'Pressure',
             yaxis_title_text = 'Power',
             zaxis_title_text = 'resistance'
            )

fig.update_layout(scene=scene1, scene2=scene2, scene3=scene3)
fig.show()

In [65]:
fig = make_subplots(
        rows=1, cols=2,
        subplot_titles = ['Objective',  'GP Objective'],
        specs=[[{'type': 'surface'}, {'type': 'surface'}]],
        print_grid=True
        )

X_obs = np.load(RESULT_DIR + "/" + str(run) + "_x_obs.npy")
xgrid = np.load(RESULT_DIR + "/" + str(run) + "_xgrid.npy")
ygrid = np.load(RESULT_DIR + "/" + str(run) + "_ygrid.npy")
parameter_grid = np.array([xgrid, ygrid])
x_suggested = np.load(RESULT_DIR+"/"+str(run)+'_x_next.npy')


# Plot Objective
obj_func_array = np.load(RESULT_DIR + "/" + str(run) + "_obj_func_array.npy")
y_obj_obs = np.load(RESULT_DIR + "/" + str(run) + "_y_obj_obs.npy")

from run import stress_obj as obj_func
with open(RESULT_DIR + "/" + str(run) + '_gp_objects.pkl', 'rb') as file:
    data = pickle.load(file)
    GP_stress = data['stress'] 
    GP_resist = data['resist'] 
    mu_s, _, mu_grad = GP_stress.posterior(x_suggested, calc_grad=True)
    mu_r, _ = GP_stress.posterior(x_suggested)
    obj_val, _, _, _, _ = obj_func(mu_s, mu_grad, mu_r)
    

val_min, val_max = add_3dsurf_plot(run, fig, 
                                   parameter_grid, obj_func_array,
                                   X_obs, y_obj_obs, 
                                  np.append(x_suggested, obj_val, axis=1),
                                   'Objective', 1)
scene1 = dict(zaxis = dict(nticks=4, range=[-.5, 1],),
#               xaxis = dict(nticks=4, range=[2, 5],),
             xaxis_title_text = 'Pressure',
             yaxis_title_text = 'Power',
             zaxis_title_text = 'value',
            )

# Plot GP Objective
obj_mu_array = np.load(RESULT_DIR + "/" + str(run) + "_obj_mu_array.npy")

with open(RESULT_DIR + "/" + str(run) + '_gp_objects.pkl', 'rb') as file:
    data = pickle.load(file)
    GP_obj = data['obj'] 
    mu, _ = GP_obj.posterior(x_suggested)

val_min, val_max = add_3dsurf_plot(run, fig, 
                                   parameter_grid, obj_mu_array,
                                   X_obs, y_obj_obs, 
                                   np.append(x_suggested, mu, axis=1),
                                   'resist', 2)

scene2 = dict(zaxis = dict(nticks=4, range=[-.5, 1],),
             xaxis_title_text = 'Pressure',
             yaxis_title_text = 'Power',
             zaxis_title_text = 'value'
            )

fig.update_layout(scene=scene1, scene2=scene2)
fig.show()

This is the format of your plot grid:
[ (1,1) scene  ]  [ (1,2) scene2 ]



## 2D view at suggested point

In [66]:
parameter_space = np.array([[2, 23], [50, 750]])
  
x_suggested = np.load(RESULT_DIR+"/"+str(run)+'_x_next.npy')

# Along Pressure axis
xx = np.linspace(parameter_space[0][0], parameter_space[0][1], 100)
xx = np.append(xx, [2, 3, 5, 8, 11, 14, 17, 20, 23, x_suggested[0, 0]])
xx = np.unique(xx)
y = np.repeat(x_suggested[0, 1], xx.shape[0])

press_ax_param = np.append(xx.reshape(-1,1), 
                           y.reshape(-1,1), 
                           axis=1)

# Along power axis
yy = np.linspace(parameter_space[1][0], parameter_space[1][1], 20)
yy = np.append(yy, [100, 500, 750, x_suggested[0, 1]])
yy = np.unique(yy)
x = np.repeat(x_suggested[0, 0], yy.shape[0])

pow_ax_param = np.append(x.reshape(-1,1), 
                         yy.reshape(-1,1), 
                         axis=1)

### Pressure axis

In [67]:
gp_stress_array = []
gp_resist_array = []
gp_slope_array = []
obj_array = []
gp_obj_array = []
acq_array = []
sd_array = []

from run import stress_obj as obj_func
with open(RESULT_DIR + "/" + str(run) + '_gp_objects.pkl', 'rb') as file:
    data = pickle.load(file)
    GP_stress = data['stress']
    GP_resist = data['resist']
    GP_obj = data['obj']
    
    for i, x in enumerate(press_ax_param):
        
        if np.isclose(x[0], x_suggested[0,0]):
            indx = i
        
        x = x.reshape(1,-1)
        mu_s, _, mu_grad = GP_stress.posterior(x, calc_grad=True)
        
        gp_stress_array.append(mu_s.item())
        gp_slope_array.append(mu_grad.item())
        
        mu_r, _ = GP_resist.posterior(x)
        gp_resist_array.append(mu_r.item())
        
        obj_val, _, _, _, _ = obj_func(mu_s, mu_grad, mu_r)
        obj_array.append(obj_val.item())
        
        mu_o, sd_o = GP_obj.posterior(x)
        gp_obj_array.append(mu_o.item())
        sd_array.append(sd_o.item())
    
gp_obj_array = np.array(gp_obj_array)
sd_array = np.array(sd_array)        

from plotly.subplots import make_subplots
import plotly.graph_objects as go

fig = make_subplots(rows=2, cols=2,
                    subplot_titles=("Stress", "Resistance", "Slope", "Obj"))

fig.add_trace(
    go.Scatter(x=press_ax_param[:,0], y=gp_stress_array, showlegend=False,
               mode='lines', line={'color': 'blue'}),
    row=1, col=1
)
fig.add_trace(
    go.Scatter(x=[press_ax_param[indx,0]], y=[gp_stress_array[indx]], showlegend=False,
                mode='markers', marker=dict(size=8, color='red'),),
    row=1, col=1
)

fig.add_trace(
    go.Scatter(x=press_ax_param[:,0], y=gp_resist_array, showlegend=False,
              mode='lines', line={'color': 'blue'}),
    row=1, col=2
)
fig.add_trace(
    go.Scatter(x=[press_ax_param[indx,0]], y=[gp_resist_array[indx]], showlegend=False,
               mode='markers', marker=dict(size=8, color='red'),),
    row=1, col=2
)


fig.add_trace(
    go.Scatter(x=press_ax_param[:,0], y=gp_slope_array, showlegend=False,
               mode='lines', line={'color': 'blue'}),
    row=2, col=1
)
fig.add_trace(
    go.Scatter(x=[press_ax_param[indx,0]], y=[gp_slope_array[indx]], showlegend=False,
                   mode='markers', marker=dict(size=8, color='red'),),
    row=2, col=1
)


fig.add_trace(
    go.Scatter(x=press_ax_param[:,0], y=obj_array, showlegend=False,
                mode='lines', line={'dash': 'dash', 'color': 'black'}),
    row=2, col=2
)
fig.add_trace(
    go.Scatter(x=press_ax_param[:,0], y=gp_obj_array, showlegend=False, 
              mode='lines', line={'color': 'blue'}),
    row=2, col=2
)

def fillcol(label):
    if label >= 1:
        return 'rgba(0,250,0,0.4)'
    else:
        return 'rgba(250,0,0,0.4)'

fig.add_trace(go.Scatter(x=press_ax_param[:, 0], y=gp_obj_array+1.96*sd_array,
                          line = dict(color='rgba(0,0,0,0)'),
                         showlegend=False),
    row=2, col=2
)

fig.add_trace(go.Scatter(x=press_ax_param[:, 0], y=gp_obj_array-1.96*sd_array,
                          line = dict(color='rgba(0,0,0,0)'),
                          fill='tonexty', 
                          fillcolor = 'rgba(0,250,0,0.4)',
                         showlegend=False),
    row=2, col=2
)
fig.add_trace(
    go.Scatter(x=[press_ax_param[indx,0]], y=[gp_obj_array[indx]], showlegend=False,
               mode='markers', marker=dict(size=8, color='red'),),
    row=2, col=2
)


fig.update_layout(height=600, width=900)
fig.show()

In [68]:
gp_stress_array = []
gp_resist_array = []
gp_slope_array = []
obj_array = []
gp_obj_array = []
acq_array = []
sd_array = []

from run import stress_obj as obj_func
with open(RESULT_DIR + "/" + str(run) + '_gp_objects.pkl', 'rb') as file:
    data = pickle.load(file)
    GP_stress = data['stress']
    GP_resist = data['resist']
    GP_obj = data['obj']
    
    for i, x in enumerate(pow_ax_param):
        
        if np.isclose(x[1], x_suggested[0,1]):
            indx = i
        
        x = x.reshape(1,-1)
        mu_s, _, mu_grad = GP_stress.posterior(x, calc_grad=True)
        
        gp_stress_array.append(mu_s.item())
        gp_slope_array.append(mu_grad.item())
        
        mu_r, _ = GP_resist.posterior(x)
        gp_resist_array.append(mu_r.item())
        
        obj_val, _, _, _, _ = obj_func(mu_s, mu_grad, mu_r)
        obj_array.append(obj_val.item())
        
        mu_o, sd_o = GP_obj.posterior(x)
        gp_obj_array.append(mu_o.item())
        sd_array.append(sd_o.item())
    
gp_obj_array = np.array(gp_obj_array)
sd_array = np.array(sd_array)    
    
from plotly.subplots import make_subplots
import plotly.graph_objects as go

fig = make_subplots(rows=2, cols=2,
                    subplot_titles=("Stress", "Resistance", "Slope", "Obj"))

fig.add_trace(
    go.Scatter(x=pow_ax_param[:,1], y=gp_stress_array, showlegend=False,
               mode='lines', line={'color': 'blue'}),
    row=1, col=1
)
fig.add_trace(
    go.Scatter(x=[pow_ax_param[indx,1]], y=[gp_stress_array[indx]], showlegend=False,
              mode='markers', marker=dict(size=8, color='red'),),
    row=1, col=1
)

fig.add_trace(
    go.Scatter(x=pow_ax_param[:,1], y=gp_resist_array, showlegend=False,
               mode='lines', line={'color': 'blue'}),
    row=1, col=2
)
fig.add_trace(
    go.Scatter(x=[pow_ax_param[indx,1]], y=[gp_resist_array[indx]], showlegend=False,
              mode='markers', marker=dict(size=8, color='red'),),
    row=1, col=2
)

fig.add_trace(
    go.Scatter(x=pow_ax_param[:,1], y=gp_slope_array, showlegend=False,
               mode='lines', line={'color': 'blue'}),
    row=2, col=1
)
fig.add_trace(
    go.Scatter(x=[pow_ax_param[indx,1]], y=[gp_slope_array[indx]], showlegend=False,
              mode='markers', marker=dict(size=8, color='red'),),
    row=2, col=1
)


fig.add_trace(
    go.Scatter(x=pow_ax_param[:,1], y=obj_array, showlegend=False,
                mode='lines', line={'dash': 'dash', 'color': 'black'}),
    row=2, col=2
)
fig.add_trace(
    go.Scatter(x=pow_ax_param[:,1], y=gp_obj_array, showlegend=False,
              mode='lines', line={'color': 'blue'}),
    row=2, col=2
)

def fillcol(label):
    if label >= 1:
        return 'rgba(0,250,0,0.4)'
    else:
        return 'rgba(250,0,0,0.4)'

fig.add_trace(go.Scatter(x=pow_ax_param[:,1], y=gp_obj_array+1.96*sd_array,
                          line = dict(color='rgba(0,0,0,0)'),
                         showlegend=False),
    row=2, col=2
)

fig.add_trace(go.Scatter(x=pow_ax_param[:,1], y=gp_obj_array-1.96*sd_array,
                          line = dict(color='rgba(0,0,0,0)'),
                          fill='tonexty', 
                          fillcolor = 'rgba(0,250,0,0.4)',
                         showlegend=False),
    row=2, col=2
)
fig.add_trace(
    go.Scatter(x=[pow_ax_param[indx,1]], y=[gp_obj_array[indx]], showlegend=False,
              mode='markers', marker=dict(size=8, color='red'),),
    row=2, col=2
)

fig.update_layout(height=600, width=950)
fig.show()